In [1]:
import keras
from keras.datasets import cifar10
from keras.preprocessing.image import ImageDataGenerator
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Conv2D, MaxPooling2D
from keras.models import load_model

Using TensorFlow backend.


In [2]:
import os
from os import path
import sys
import time
import numpy as np
import matplotlib.pyplot as plt
% matplotlib inline
import PIL
from IPython.display import Image 
from sklearn.model_selection import train_test_split

In [3]:
base_dir = "~/ConvNet/"

In [4]:
sys.path.append(path.abspath('~/CIFAR_10/'))
import data_transform_module as dtm

### Supporting functions

**For model saving**

In [5]:
def saveModelInfo(model_name, model, model_history, path):
    
    mdl = "model_"+model_name+".h5"
    wgt = "weight_"+model_name+".h5"
    hst = "history_"+model_name+".p"
    
    model.save(path+mdl) 
    model.save_weights(path+wgt)
    dtm.pickleSomething(model_history, path, hst)

**For data loading and preprocessing**

In [6]:
def scaleData(data_array):
    data_array = data_array.astype('float32')
    data_array /= 255.
    return data_array
    
def data_load_split():
    """cifar data loaded from from keras, shuffled and 
       split to train, test and validation sets"""
    
    (xx_train, yy_train), (x_test, y_test) = cifar10.load_data()
    
    yy_train = keras.utils.to_categorical(yy_train, num_classes=10) # binary class matrix
    y_test = keras.utils.to_categorical(y_test, num_classes=10)
    
    xx_train = scaleData(xx_train)
    x_test = scaleData(x_test)
    
    x_train, x_val, y_train, y_val = train_test_split(xx_train, yy_train, test_size=0.1, random_state=42)
    
    return x_train, y_train, x_val, y_val, x_test, y_test

### Load and preprocess data

In [7]:
x_train, y_train, x_val, y_val, x_test, y_test = data_load_split()

In [20]:
y_test.shape


(10000, 10)

### Modeling

**Define a sequential model**

In [8]:
augment = 1 
model_name = "1"
save_model_info = 1
model_path = base_dir+"ModelInfo/"

In [9]:
image_shape = (32, 32, 3)

In [10]:
model = Sequential()

model.add(Conv2D(32, (3, 3), input_shape=(32, 32, 3)))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))


model.add(Conv2D(64, (3, 3)))
model.add(Activation('relu'))

model.add(Conv2D(64, (3, 3)))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))

model.add(Flatten())  
model.add(Dense(512))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(10))
model.add(Activation('softmax'))

**Compile the defined sequential model**

In [11]:
opt = keras.optimizers.rmsprop(lr=0.001, decay=1e-6)
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

**Image Augmentation** (optional) 

In [12]:
# the following augmentation configuration will be applied during training
datagen = ImageDataGenerator(
        rotation_range=5.,
        shear_range=0,
        zoom_range=0,
        fill_mode='reflect',
        width_shift_range=0.1,  
        height_shift_range=0.1,
        horizontal_flip=True,
        vertical_flip=True)

**Fit model**  
* record model history  
* save model
* save model weights

In [13]:
start = time.time()

if augment:   
    print("Augmenting images on the fly during training ...\n")
    model_history = model.fit_generator(datagen.flow(x_train, y_train, batch_size = 96),
                                 samples_per_epoch = x_train.shape[0], epochs = 99, 
                                 validation_data=(x_val, y_val))
else:
    print("No augmenting during training ...\n")
    model_history = model.fit(x_train, y_train, 
                          batch_size=96, 
                          epochs=99, 
                          validation_data = (x_val, y_val),
                          shuffle=True,
                          verbose=1)

end = time.time()
print("Model took %0.2f seconds to train"%(end - start))


if save_model_info:
    if model_name:
        saveModelInfo(model_name, model, model_history.history, model_path)
    else:
        saveModelInfo("", model, model_history.history, model_path)

Augmenting images on the fly during training ...



/Users/susmitadatta/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:7: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<keras.pre..., epochs=99, validation_data=(array([[[..., steps_per_epoch=468)`


Epoch 1/99
468/468 [==============================] - 121s - loss: 1.6723 - acc: 0.3829 - val_loss: 1.2989 - val_acc: 0.5226

**NOTE:** Model information has been saved in the following directory. 

In [16]:
print(model_path)

/Users/susmitadatta/Metis/Proj03/CNN_CIFAR10/ModelInfo/


The save model can be loaded and applied to test images.

### Apply Model on Test Images

In [24]:
acc_score = model.evaluate(x_test, y_test, verbose=0)
y_pred_prob = model.predict(x_test)
y_pred_class = model.predict_classes(x_test)

 9952/10000 [============================>.] - ETA: 0s

In [25]:
print("Accuracy:", acc_score[1])

Accuracy: 0.8313


In [26]:
pred_path = base_dir+"PredInfo/"
dtm.pickleSomething(acc_score, pred_path, "acc_"+model_name+".p")
dtm.pickleSomething(y_pred_prob, pred_path, "prob_"+model_name+".p")
dtm.pickleSomething(y_pred_class, pred_path, "class_"+model_name+".p")

**NOTE:** Prediction information has been saved in the following directory.

In [23]:
print(pred_path)

/Users/susmitadatta/Metis/Proj03/CNN_CIFAR10/PredInfo/


**Check validation and training accuracy**

In [33]:
val_acc = model.evaluate(x_val, y_val, verbose=0)
print("Accuracy on the validation set:", val_acc[1])

Accuracy on the validation set: 0.841


In [34]:
train_acc = model.evaluate(x_train, y_train, verbose=0)
print("Accuracy on the training set:", train_acc[1])

Accuracy on the training set: 0.914266666667
